In [2]:
pip install mclp
pip install folium pandas
pip install pulp
pip install geopy

  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Created wheel for mclp: filename=mclp-1.0-py3-none-any.whl size=2149 sha256=dbe265a1f4c927862f8c216ab95b5e29643bb2f6e06c5dad4833633848bb49aa
  Stored in directory: c:\users\administrator\appdata\local\pip\cache\wheels\eb\11\35\b852d845e983a48663e3035157b26e69990a06509ddf32c904
Successfully built mclp
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.0 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [66]:
import pandas as pd
import folium
from pulp import LpProblem, LpMaximize, LpVariable, lpSum, LpBinary
from geopy.distance import geodesic
from sklearn.preprocessing import MinMaxScaler

In [79]:
bus_df = pd.read_csv("노선_요약.csv")
subway_df = pd.read_csv("지하철_요약.csv")
cafe_df = pd.read_csv("데이터\입지후보데이터\일반음식점(카페)현황.csv", encoding = 'CP949')
park_df = pd.read_csv("데이터\입지후보데이터\도시공원정보현황(제공표준).csv", encoding = 'CP949')

In [84]:
cafe_df = cafe_df[(cafe_df['시군명'] == '성남시') & (cafe_df['영업상태명'] == '영업')]
cafe_df = cafe_df.rename(columns = {'WGS84위도' : '위도','WGS84경도': '경도'})
# 시설규모 바탕으로 가중치 생성
scaler = MinMaxScaler()
cafe_df['가중치'] = scaler.fit_transform(cafe_df[['총시설규모(㎡)']])
cafe_df

시군명                사업장명     인허가일자 영업상태명 폐업일자  총시설규모(㎡) 위생업태명  \
1909  성남시         챠오바 라이트 판교점  20130531    영업  NaN     59.84    까페   
1910  성남시                커피나무  20120314    영업  NaN     32.64    까페   
1911  성남시     알레그리아(판교테크노밸리점)  20120820    영업  NaN     44.55    까페   
1912  성남시  블루스엘리(Blues Alley)  20081202    영업  NaN     91.98    까페   
1913  성남시     더레빗(The rabbit)  20060413    영업  NaN    108.97    까페   
...   ...                 ...       ...   ...  ...       ...   ...   
1991  성남시                  아바  20020821    영업  NaN    182.17    까페   
1992  성남시             아트모스 커피  20120802    영업  NaN    107.93    까페   
1993  성남시            갤러리아 라이브  19991230    영업  NaN     45.14    까페   
1994  성남시         투썸플레이스분당구미점  20130226    영업  NaN    164.34    까페   
1995  성남시               카페아지트  20150619    영업  NaN     33.63    까페   

                                            소재지도로명주소  \
1909   경기도 성남시 분당구 대왕판교로 660 (삼평동, 유스페이스1.  1층 125호)   
1910                   경기도 성남시 수정구 수정로 160, 1층 (신흥동)   
1911      경기도 성남시 분당구 판교역로 230 (삼평동, 삼환하이펙스 B동 119호)   
1912              경기도 성남시 분당구 느티로87번길 6 (정자동, 지하1층 )   
1913  경기도 성남시 분당구 성남대로331번길 3-9 (정자동,백궁프라자3    309호)   
...                                              ...   
1991            경기도 성남시 분당구 야탑로 106 (야탑동,프리아오피스텔지하1)   
1992          경기도 성남시 분당구 서판교로44번길 17-5 (판교동, 1층 일부)   
1993                경기도 성남시 분당구 불정로420번길 4 (서현동, 지하)   
1994         경기도 성남시 분당구 미금로 39 (구미동, 로얄프라자 1층 104호)   
1995                경기도 성남시 수정구 수정남로62번길 3, 1층 (수진동)   

                                      소재지지번주소  소재지우편번호         위도          경도  \
1909   경기도 성남시 분당구 삼평동 670번지 유스페이스1.  1층 125호      NaN  37.400611  127.106932   
1910               경기도 성남시 수정구 신흥동 5536번지 1층       NaN  37.442414  127.137760   
1911     경기도 성남시 분당구 삼평동 679번지 삼환하이펙스 B동 119호      NaN  37.401221  127.110378   
1912               경기도 성남시 분당구 정자동 61-4 지하1층       NaN  37.369165  127.114441   
1913  경기도 성남시 분당구 정자동 156-2번지 백궁프라자3    309호       NaN  37.364760  127.107628   
...                                       ...      ...        ...         ...   
1991      경기도 성남시 분당구 야탑동 514-4번지 프리아오피스텔지하1       NaN  37.409499  127.130540   
1992             경기도 성남시 분당구 판교동 567-4 1층 일부       NaN  37.391235  127.099597   
1993               경기도 성남시 분당구 서현동 334-3번지 지하      NaN  37.376196  127.140216   
1994    경기도 성남시 분당구 구미동 204-2번지 로얄프라자 1층 104호      NaN  37.336757  127.115905   
1995                경기도 성남시 수정구 수진동 451번지 1층       NaN  37.440660  127.134819   

           가중치  
1909  0.093523  
1910  0.035709  
1911  0.061024  
1912  0.161838  
1913  0.197951  
...        ...  
1991  0.353540  
1992  0.195740  
1993  0.062278  
1994  0.315642  
1995  0.037813  

[87 rows x 13 columns]

In [88]:
park_df = park_df[park_df['소재지지번주소'].str.startswith('경기도 성남시')]
park_df['가중치'] = scaler.fit_transform(park_df[['공원면적(㎡)']])
park_df = park_df.dropna(subset=['위도', '경도'])
park_df.isnull().sum()

공원명               0
공원구분              0
소재지도로명주소        166
소재지지번주소           0
위도                0
경도                0
공원면적(㎡)           0
공원보유시설(운동시설)     58
공원보유시설(유희시설)     63
공원보유시설(편익시설)     33
공원보유시설(교양시설)    180
공원보유시설(기타시설)    192
지정고시일             0
관리기관명             0
전화번호              0
데이터기준일자           0
가중치               0
dtype: int64

In [80]:
bus_df = bus_df.dropna()
bus_df['혼잡도'] = bus_df['환승시간(분)']*bus_df['노선개수']
bus_df['가중치'] = scaler.fit_transform(bus_df[['혼잡도']])
bus_df

정류장명    환승시간(분)                 상세위치         위도          경도  \
0           판교제2테크노밸리   7.990000            한국도로공사본사앞  37.411683  127.099350   
1           판교제2테크노밸리   7.990000           한국도로공사본사건너  37.411333  127.099733   
2              동산마을입구  13.270000         시흥지하차도변 성남방면  37.422467  127.101233   
3              동산마을입구  13.270000         시흥지하차도변 서울방면  37.422800  127.101400   
4     성남농협대왕지점.고등동우체국  11.752799              고등동자치센터  37.428217  127.101650   
...               ...        ...                  ...        ...         ...   
1287          판교대장로동측   9.330000            판교대장지구 초입  37.363317  127.067800   
1288         판교풍경채5단지  19.300000         대장동 판교풍경채5단지  37.365000  127.069100   
1289    힐스테이트판교엘포레4단지  20.520000    대장동 힐스테이트판교엘포레4단지  37.365233  127.068883   
1290   판교반디유치원.복합문화단지  24.220000   대장동 판교반디유치원.복합문화단지  37.366867  127.070883   
1291     판교더샵포레스트11단지  13.034458  대장동 판교더샵포레스트11단지 부근  37.367350  127.071117   

                                            시내버스_경유노선번호 시외버스_경유노선번호  \
0     P9243(퇴근)(시내),5700A(시내),55(시내),P9242(퇴근)(시내),6...        해당없음   
1     5600(시내),P9241(출근)(시내),P9243(출근)(시내),1009(시내),...        해당없음   
2                            9800(시내),9409(서울),9400(시내)        해당없음   
3                                     9400(시내),9800(시내)        해당없음   
4     누리2(시내),1009(시내),6900(시내),342(시내),57(시내),5700A...        해당없음   
...                                                 ...         ...   
1287  310(시내),9507(시내),32(마을),4103(시내),9409(서울),380(...        해당없음   
1288  9409(서울),9507(시내),340(시내),32(마을),73(마을),380(시내...        해당없음   
1289  310(시내),32(마을),9507(시내),340(시내),380(시내),9409(서...        해당없음   
1290  310(시내),340(시내),380(시내),9409(서울),9507(시내),32(마...        해당없음   
1291  310(시내),9507(시내),340(시내),9409(서울),4103(시내),73(...        해당없음   

      시내버스_노선개수  시외버스_노선개수  노선개수         혼잡도       가중치  
0            27          0    27  215.730000  0.535547  
1            20          0    20  159.800000  0.396029  
2             3          0     3   39.810000  0.096712  
3             2          0     2   26.540000  0.063610  
4            13          0    13  152.786392  0.378533  
...         ...        ...   ...         ...       ...  
1287          8          0     8   74.640000  0.183596  
1288          8          0     8  154.400000  0.382558  
1289          7          0     7  143.640000  0.355717  
1290          7          0     7  169.540000  0.420325  
1291          8          0     8  104.275664  0.257523  

[1282 rows x 12 columns]

In [83]:
subway_df['일평균승하차인원'] = subway_df['승차총승객수'] + subway_df['하차총승객수']
subway_df['가중치'] = scaler.fit_transform(subway_df[['일평균승하차인원']])
subway_df

역사_ID    역사명          호선         위도          경도        승차총승객수  \
0    9008     성남  수도권 광역급행철도  37.394670  127.120580   1131.290323   
1    1512     성남         경강선  37.394680  127.119450   1131.290323   
2    4313     미금    신분당선(연장)  37.349982  127.108918  14675.322581   
3    1858     미금         분당선  37.350077  127.108910  14675.322581   
4    4312     정자        신분당선  37.367098  127.108403  17094.258065   
5    1857     정자         분당선  37.365994  127.108070  17094.258065   
6    4311     판교        신분당선  37.394761  127.112217   5533.225806   
7    1501     판교         경강선  37.394761  127.111217   5533.225806   
8    2828    남위례         8호선  37.462400  127.139770   7322.322581   
9    2827     모란         8호선  37.433824  127.129837  12927.306452   
10   1853     모란         분당선  37.432052  127.129104  12927.306452   
11   2826     수진         8호선  37.437428  127.140722   5548.870968   
12   2825     신흥         8호선  37.440918  127.147564   5244.419355   
13   2824  단대오거리         8호선  37.445210  127.156866  12073.806452   
14   2822     산성         8호선  37.457122  127.149908   6092.096774   
15   2821     복정         8호선  37.471052  127.126732   4949.213115   
16   1031     복정         분당선  37.470345  127.126658   4949.213115   
17   1860     이매         분당선  37.395371  127.128248   3288.967742   
18   1502     이매         경강선  37.394655  127.127819   3288.967742   
19   1859     오리         분당선  37.339824  127.108942  10560.096774   
20   1856     수내         분당선  37.378455  127.114322  12525.000000   
21   1855     서현         분당선  37.385126  127.123592  22729.225806   
22   1854     야탑         분당선  37.411185  127.128715  24656.258065   
23   1852     태평         분당선  37.440019  127.127709  12867.935484   
24   1851    가천대         분당선  37.448605  127.126697  12083.903226   

          하차총승객수      일평균승하차인원       가중치  
0     984.322581   2115.612903  0.000000  
1     984.322581   2115.612903  0.000000  
2   15195.387097  29870.709677  0.571278  
3   15195.387097  29870.709677  0.571278  
4   17808.193548  34902.451613  0.674845  
5   17808.193548  34902.451613  0.674845  
6    5273.419355  10806.645161  0.178886  
7    5273.419355  10806.645161  0.178886  
8    7303.677419  14626.000000  0.257499  
9   12608.483871  25535.790323  0.482053  
10  12608.483871  25535.790323  0.482053  
11   5149.806452  10698.677419  0.176664  
12   5351.612903  10596.032258  0.174551  
13  11409.322581  23483.129032  0.439804  
14   6213.741935  12305.838710  0.209744  
15   4238.098361   9187.311475  0.145555  
16   4238.098361   9187.311475  0.145555  
17   3086.725806   6375.693548  0.087684  
18   3086.725806   6375.693548  0.087684  
19   9099.387097  19659.483871  0.361102  
20  12488.483871  25013.483871  0.471303  
21  23208.129032  45937.354839  0.901975  
22  26043.580645  50699.838710  1.000000  
23  12455.548387  25323.483871  0.477683  
24  12187.161290  24271.064516  0.456022

In [97]:
# 이름 통일
bus_df = bus_df.rename(columns = {'정류장명':'이름'}) 
subway_df = subway_df.rename(columns = {'역사명':'이름'}) 
cafe_df = cafe_df.rename(columns = {'사업장명':'이름'}) 
park_df = park_df.rename(columns = {'공원명':'이름'}) 

In [110]:
# 필요한 열만 추출
bus_coords = bus_df[['위도', '경도','가중치','이름']].copy()
subway_coords = subway_df[['위도', '경도','가중치','이름']].copy()
cafe_coords = cafe_df[['위도', '경도','가중치','이름']].copy()
park_coords = park_df[['위도', '경도','가중치','이름']].copy()

# 두 데이터프레임을 위로 붙이기
all_df = pd.concat([bus_coords, subway_coords,cafe_coords,park_coords], ignore_index=True)
all_df

candidate_df = pd.concat([bus_df, park_df], ignore_index=True)

print(candidate_df)

                   이름    환승시간(분)          상세위치         위도          경도  \
0           판교제2테크노밸리   7.990000     한국도로공사본사앞  37.411683  127.099350   
1           판교제2테크노밸리   7.990000    한국도로공사본사건너  37.411333  127.099733   
2              동산마을입구  13.270000  시흥지하차도변 성남방면  37.422467  127.101233   
3              동산마을입구  13.270000  시흥지하차도변 서울방면  37.422800  127.101400   
4     성남농협대왕지점.고등동우체국  11.752799       고등동자치센터  37.428217  127.101650   
...               ...        ...           ...        ...         ...   
1486             하얀공원        NaN           NaN  37.344885  127.118069   
1487             오리공원        NaN           NaN  37.344557  127.114146   
1488             구미공원        NaN           NaN  37.337391  127.117303   
1489             연꽃공원        NaN           NaN  37.415308  127.137469   
1490             매향공원        NaN           NaN  37.414710  127.137412   

                                            시내버스_경유노선번호 시외버스_경유노선번호  \
0     P9243(퇴근)(시내),5700A(시내),55(시내),P9242(퇴근)(시내),6

In [98]:
# 지도 중심은 첫 번째 버스 정류장
m = folium.Map(location=[bus_df['위도'].iloc[0], bus_df['경도'].iloc[0]], zoom_start=14)

# 버스 정류장 시각화 (파란색)
for _, row in bus_df.iterrows():
    folium.CircleMarker(
        location=[row['위도'], row['경도']],
        radius=5,
        popup=row['이름'],
        color='blue',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)

# 지하철 역사 시각화 (빨간색)
for _, row in subway_df.iterrows():
    folium.CircleMarker(
        location=[row['위도'], row['경도']],
        radius=6,
        popup=row['이름'],
        color='red',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)

# 카페 시각화 (노란색)
for _, row in cafe_df.iterrows():
    folium.CircleMarker(
        location=[row['위도'], row['경도']],
        radius=6,
        popup=row['이름'],
        color='yellow',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)

# 공원 시각화 (초록색)
for _, row in park_df.iterrows():
    folium.CircleMarker(
        location=[row['위도'], row['경도']],
        radius=6,
        popup=row['이름'],
        color='green',
        fill=True,
        fill_opacity=0.7
    ).add_to(m)

# 결과 지도 출력
m

In [105]:
# 수요지점과 후보지점 
demand_points = list(zip(all_df['위도'], all_df['경도'], all_df['가중치'], all_df['이름']))  # 카페, 공원, 버스정류장, 지하철 위치 및 가중치

candidate_bins = list(zip(candidate_df['위도'], candidate_df['경도'], candidate_df['이름']))  # 후보지는 공원이랑 버스정류장

# 거리 행렬
distance_matrix = [
    [geodesic(dp[:2], cb[:2]).meters for cb in candidate_bins]
    for dp in demand_points
]

# 파라미터 설정
coverage_radius = 150  # meters
p = 1000  # 쓰레기통 설치 개수 제한

# 이진 변수
x = [LpVariable(f"x_{j}", cat=LpBinary) for j in range(len(candidate_bins))]  # 후보지 설치 여부
y = [LpVariable(f"y_{i}", cat=LpBinary) for i in range(len(demand_points))]  # 수요지 커버 여부

# 모델 생성
model = LpProblem("MCLP_Weighted", LpMaximize)

# 목적 함수: 커버된 수요의 가중치 총합 최대화
model += lpSum([demand_points[i][2] * y[i] for i in range(len(demand_points))])

# 제약 1: 반경 내 후보지점이 있어야 커버 인정
for i in range(len(demand_points)):
    model += lpSum([x[j] for j in range(len(candidate_bins)) if distance_matrix[i][j] <= coverage_radius]) >= y[i]

# 제약 2: 설치 개수 제한
model += lpSum(x) <= p

# 최적화 수행
model.solve()


1

In [112]:
import folium

# 지도 중심을 전체 수요지점 평균으로
center_lat = sum([dp[0] for dp in demand_points]) / len(demand_points)
center_lon = sum([dp[1] for dp in demand_points]) / len(demand_points)

# 지도 초기화
m = folium.Map(location=[center_lat, center_lon], zoom_start=14)

# 수요지점 시각화
for i, (lat, lon, weight, name) in enumerate(demand_points):
    covered = y[i].varValue > 0.5
    folium.CircleMarker(
        location=[lat, lon],
        radius=4 + weight * 10,  # 가중치 기반 크기
        color='black' if covered else 'lightgray',  # 커버 여부에 따라 테두리
        fill=True,
        fill_color='orange' if covered else 'white',
        fill_opacity=0.8,
        tooltip=name,
        popup=f"가중치: {round(weight, 3)}"
    ).add_to(m)

# 설치된 쓰레기통 위치 마커
for j, (lat, lon, name) in enumerate(candidate_bins):
    if x[j].varValue > 0.5:
        folium.Marker(
            location=[lat, lon],
            icon=folium.Icon(color='red', icon='trash', prefix='fa'),
            tooltip=name,
            popup=f"설치 위치: {name}"
        ).add_to(m)

# 지도 출력
m


In [108]:
# 쓰레기통 설치 결과를 DataFrame으로 저장
result_df = pd.DataFrame(candidate_bins, columns=['위도', '경도', '이름'])
result_df['설치여부'] = [int(var.varValue) for var in x]

# 설치된 위치만 필터링
installed_bins = result_df[result_df['설치여부'] == 1]

# CSV로 저장
installed_bins.to_csv("mclp_installed_bins.csv", index=False, encoding = "CP949")